How to use:  
1) Fill up raw_backgrounds image on your drive folder with items you wish to process
2) Run Stage 0 and 1
You now have the created items!
//---//
3) For finding the best items among the created bunch, use Stage 2 and Stage 3 (up to preference)

##Stage 0: Process Raw images into square backgrounds

In [ ]:
# ─────────────────────────────────────────────────────────────────────────────
#  GOOGLE COLAB – FINAL VERSION (macOS junk skipped, radial edge bias)
# ─────────────────────────────────────────────────────────────────────────────
# @title **Crop & Pad Settings** { run: "auto" }
padding_percent = 90   # @param {type:"slider", min:50, max:250, step:5}
edge_bias       = 65   # @param {type:"slider", min:0,   max:100, step:5}

# ─────────────────────────────────────────────────────────────────────────────
from google.colab import drive
drive.mount('/content/drive', force_remount=True)

import os, random, zipfile, shutil, math
from pathlib import Path
from PIL import Image

# ─────────────────────────────────────────────────────────────────────────────
RAW_DRIVE = '/content/drive/MyDrive/backgrounds_raw'
OUT_DRIVE = '/content/drive/MyDrive/backgrounds_cropped'
ZIP_OUT   = '/content/drive/MyDrive/backgrounds_cropped_squares.zip'

FRAME_SIZE = 1024
STEP_SIZE  = 512
PAD_COLOR  = (24, 24, 24)                     # #181818
EXTS       = ('.jpg','.jpeg','.JPG','.JPEG','.webp','.WEBP')

# clean previous run
os.makedirs(OUT_DRIVE, exist_ok=True)
for f in os.listdir(OUT_DRIVE): os.remove(os.path.join(OUT_DRIVE, f))
if os.path.exists(ZIP_OUT): os.remove(ZIP_OUT)

target_size = int(FRAME_SIZE * (padding_percent / 100.0))
print(f"Padding % = {padding_percent} → scale largest side to {target_size}px")
print(f"Edge Bias = {edge_bias}% → radial bias in 1024×1024 canvas")

# ─────────────────────────────────────────────────────────────────────────────
zip_paths = [os.path.join(RAW_DRIVE, f) for f in os.listdir(RAW_DRIVE)
             if f.lower().endswith('.zip')]

if not zip_paths:
    print("No zip files found – nothing to do.")
else:
    print(f"Found {len(zip_paths)} zip file(s):")
    for p in zip_paths: print("  •", os.path.basename(p))

# ─────────────────────────────────────────────────────────────────────────────
def is_macos_junk(path: str) -> bool:
    """Return True for __MACOSX, .DS_Store, ._AppleDouble files, etc."""
    name = os.path.basename(path).lower()
    return (
        '__macosx' in path.lower() or
        name.startswith('._') or
        name == '.ds_store' or
        name.endswith('~')
    )

def radial_pad(img, target_w, target_h, bias_percent):
    w, h = img.size
    if w == 0 or h == 0:
        return Image.new('RGB', (target_w, target_h), PAD_COLOR)

    # uniform random when bias = 0
    if bias_percent <= 0:
        pad_l = random.randint(0, target_w - w)
        pad_t = random.randint(0, target_h - h)
    else:
        max_dist = math.hypot(target_w / 2, target_h / 2)
        attempts = 0
        while attempts < 1000:
            pad_l = random.randint(0, target_w - w)
            pad_t = random.randint(0, target_h - h)
            cx = pad_l + w / 2
            cy = pad_t + h / 2
            dist = min(cx, target_w - cx, cy, target_h - cy)
            prob = (1 - dist / max_dist) ** (bias_percent / 20.0)
            if random.random() < prob:
                break
            attempts += 1
        else:                               # fallback
            pad_l = random.randint(0, target_w - w)
            pad_t = random.randint(0, target_h - h)

    canvas = Image.new('RGB', (target_w, target_h), PAD_COLOR)
    canvas.paste(img, (pad_l, pad_t))
    return canvas

# ─────────────────────────────────────────────────────────────────────────────
with zipfile.ZipFile(ZIP_OUT, 'w') as master_zip:
    total_frames = 0

    for zip_idx, zip_path in enumerate(zip_paths, 1):
        temp_dir = f'/content/raw_zip_{zip_idx}'
        os.makedirs(temp_dir, exist_ok=True)
        print(f"\n[{zip_idx}/{len(zip_paths)}] Extracting {os.path.basename(zip_path)}")
        with zipfile.ZipFile(zip_path, 'r') as z:
            z.extractall(temp_dir)

        for root, _, files in os.walk(temp_dir):
            for filename in files:
                img_path = os.path.join(root, filename)

                # ---- SKIP macOS junk -------------------------------------------------
                if is_macos_junk(img_path):
                    continue

                if not filename.lower().endswith(EXTS):
                    continue

                try:
                    with Image.open(img_path) as im:
                        img = im.convert('RGB')
                        orig_w, orig_h = img.size

                    max_side = max(orig_w, orig_h)
                    scale = target_size / max_side
                    new_w = int(orig_w * scale)
                    new_h = int(orig_h * scale)
                    img_resized = img.resize((new_w, new_h), Image.LANCZOS)

                    print(f"  → {filename} ({orig_w}×{orig_h}) → {new_w}×{new_h}")

                    # ---- PAD INTO 1024×1024 ------------------------------------------------
                    if new_w <= FRAME_SIZE and new_h <= FRAME_SIZE:
                        final_img = radial_pad(img_resized, FRAME_SIZE, FRAME_SIZE, edge_bias)
                        name = f"zip{zip_idx}_{Path(filename).stem}_f0.jpg"
                        out_path = os.path.join(OUT_DRIVE, name)
                        final_img.save(out_path, "JPEG", quality=100)
                        master_zip.write(out_path, arcname=name)
                        total_frames += 1
                        print(f"      padded → 1 frame")

                    # ---- CROP SLIDING WINDOWS ------------------------------------------------
                    else:
                        frame_cnt = 0
                        for y in range(0, new_h - FRAME_SIZE + 1, STEP_SIZE):
                            for x in range(0, new_w - FRAME_SIZE + 1, STEP_SIZE):
                                crop = img_resized.crop((x, y, x + FRAME_SIZE, y + FRAME_SIZE))
                                name = f"zip{zip_idx}_{Path(filename).stem}_f{frame_cnt}.jpg"
                                out_path = os.path.join(OUT_DRIVE, name)
                                crop.save(out_path, "JPEG", quality=100)
                                master_zip.write(out_path, arcname=name)
                                frame_cnt += 1
                                total_frames += 1
                        print(f"      cropped → {frame_cnt} frame(s)")

                except Exception as e:
                    print(f"  [ERROR] {filename}: {e}")

        shutil.rmtree(temp_dir, ignore_errors=True)

print("\n=== ALL DONE ===")
print(f"Total 1024×1024 crops : {total_frames}")
print(f"Saved in               : {OUT_DRIVE}")
print(f"ZIP archive            : {ZIP_OUT}")

##Stage 1: Randomly add panels to the newly created backgrounds using rembg

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
# @title 1. Setup & Unzip Manga Images

!pip install rembg pillow numpy onnxruntime -q

from google.colab import drive
drive.mount('/content/drive')

import os, random, zipfile, shutil
from pathlib import Path
from PIL import Image
import numpy as np
from rembg import remove

# === CONFIG ===
MANGA_ZIP = '/content/drive/MyDrive/backgrounds_cropped3.zip' #@param {type:'string'}
BG_FOLDER = '/content/drive/MyDrive/backgrounds_final_rounded3'  # From previous step
OUTPUT_FOLDER = '/content/manga_on_bg'

# Generate a random 5-digit number for unique ZIP name
random_suffix = random.randint(10000, 99999)
ZIP_OUTPUT = f'/content/drive/MyDrive/manga_on_backgrounds_{random_suffix}.zip'

# Unzip manga images
!unzip -q "$MANGA_ZIP" -d /content/

# Clean & recreate output folder
if os.path.exists(OUTPUT_FOLDER):
    shutil.rmtree(OUTPUT_FOLDER)
os.makedirs(OUTPUT_FOLDER, exist_ok=True)

print("Manga images extracted to /content/")
print(f"Backgrounds folder: {BG_FOLDER}")
print(f"Output will be saved to: {ZIP_OUTPUT}")

In [ ]:
# @title 2. Process: Place **2 Random Manga Panels** on **Random Backgrounds**

# @markdown **Number of composite images to generate:**
num_images_to_create = 169 #@param {type:"slider", min:1, max:1000, step:1}



import os, random, math, zipfile
import numpy as np
from PIL import Image
from rembg import remove
from pathlib import Path

# ------------------------------------------------------------------
# 1. Load & SHUFFLE background images
# ------------------------------------------------------------------
all_bgs = [
    os.path.join(BG_FOLDER, f)
    for f in os.listdir(BG_FOLDER)
    if f.lower().endswith(('.png', '.jpg', '.jpeg'))
]
if not all_bgs:
    raise ValueError(f"No background images found in {BG_FOLDER}")

random.shuffle(all_bgs)                     # different order every run
all_bgs = all_bgs[:num_images_to_create]   # respect slider

print(f"Will generate {len(all_bgs)} composite images (slider limit: {num_images_to_create})")

# ------------------------------------------------------------------
# 2. Gather *all* manga file paths (no processing yet)
# ------------------------------------------------------------------
manga_paths = [
    os.path.join('/content', f)
    for f in os.listdir('/content')
    if f.lower().endswith(('.jpg', '.jpeg', '.png'))
    and not f.startswith('.')
    and os.path.isfile(os.path.join('/content', f))
]
if len(manga_paths) < 2:
    raise ValueError(f"Need at least 2 manga panels, found {len(manga_paths)}")

print(f"Found {len(manga_paths)} raw manga panels (backgrounds will be removed on-the-fly)")

# ------------------------------------------------------------------
# 3. Helper: remove BG + resize + optional flip
# ------------------------------------------------------------------
def prepare_panel(panel_path, target_h, bg_w):
    """Open → remove BG → resize to target height → random flip → return ready image + meta."""
    with Image.open(panel_path).convert("RGBA") as img:
        # ---- remove background ----
        img_np = np.array(img)
        nobg = remove(img_np)
        panel = Image.fromarray(nobg).convert("RGBA")

        # ---- resize to background height ----
        ratio = target_h / panel.height
        new_w = int(panel.width * ratio)
        panel = panel.resize((new_w, target_h), Image.LANCZOS)

        # ---- random horizontal flip ----
        flip = random.random() < 0.5
        if flip:
            panel = panel.transpose(Image.FLIP_LEFT_RIGHT)
        flip_desc = "flip" if flip else "noflip"

        # ---- decide side (left / right) ----
        # we will assign later when we know the other panel's width
        return panel, new_w, flip_desc, os.path.basename(panel_path)

# ------------------------------------------------------------------
# 4. Create composites
# ------------------------------------------------------------------
os.makedirs(OUTPUT_FOLDER, exist_ok=True)

with zipfile.ZipFile(ZIP_OUTPUT, 'w', zipfile.ZIP_DEFLATED) as zipf:
    for bg_idx, bg_path in enumerate(all_bgs, 1):
        bg_name = os.path.basename(bg_path)
        print(f"\nProcessing {bg_idx}/{len(all_bgs)}: {bg_name}")

        # ---- open background ----
        with Image.open(bg_path).convert("RGBA") as bg_img:
            bg = bg_img.copy()
            target_h = bg.height
            bg_w = bg.width

        # ---- pick 2 *different* manga files ----
        panel_a_path, panel_b_path = random.sample(manga_paths, k=2)

        # ---- prepare both panels (rembg happens *here*) ----
        panel_a_img, a_w, a_flip, a_name = prepare_panel(panel_a_path, target_h, bg_w)
        panel_b_img, b_w, b_flip, b_name = prepare_panel(panel_b_path, target_h, bg_w)

        # ---- assign sides (left / right) ----
        # put narrower panel on the side that gives more overlap-prevention
        if a_w < b_w:
            left_img, left_w, left_flip, left_name = panel_a_img, a_w, a_flip, a_name
            right_img, right_w, right_flip, right_name = panel_b_img, b_w, b_flip, b_name
        else:
            left_img, left_w, left_flip, left_name = panel_b_img, b_w, b_flip, b_name
            right_img, right_w, right_flip, right_name = panel_a_img, a_w, a_flip, a_name

        # ---- paste ----
        result = bg.copy()
        result.paste(left_img,  (0, 0),               left_img)   # left side
        result.paste(right_img, (bg_w - right_w, 0), right_img)  # right side

        # ---- build filename ----
        clean_l = Path(left_name).stem[:20]
        clean_r = Path(right_name).stem[:20]
        combined_name = f"bg{bg_idx:03d}_{clean_l}_left_{left_flip}_AND_{clean_r}_right_{right_flip}.png"
        out_path = os.path.join(OUTPUT_FOLDER, combined_name)

        result.convert("RGB").save(out_path, "PNG")
        zipf.write(out_path, combined_name)

        print(f"  [Saved] {combined_name}")

print(f"\nAll done! Generated {len(all_bgs)} composite images.")
print(f"ZIP → {ZIP_OUTPUT}")
print(f"Files → {OUTPUT_FOLDER}")


In [ ]:
from google.colab import runtime
runtime.unassign()




In [ ]:
# ─────────────────────────────────────────────────────────────────────────────
#  GOOGLE COLAB – 3-COLUMN TRIPLETS WITH EXACT CENTER-CROP FILL
# ─────────────────────────────────────────────────────────────────────────────
# @title **Triplet Generator – Exact Center-Crop Fill** { run: "auto" }
padding_to_edge         = 20   # @param {type:"slider", min:20, max:150, step:10}  "Horizontal padding (left/right)"
padding_to_top_bottom   = 20   # @param {type:"slider", min:20, max:200, step:10}  "Vertical padding (top/bottom)"
corner_radius           = 40   # @param {type:"slider", min:0, max:100, step:5}
output_count            = 10   # @param {type:"slider", min:1, max:50, step:1}

# ─────────────────────────────────────────────────────────────────────────────
from google.colab import drive
drive.mount('/content/drive', force_remount=True)

import os, random, zipfile, shutil
from pathlib import Path
from PIL import Image, ImageDraw

# ─────────────────────────────────────────────────────────────────────────────
RAW_DRIVE = '/content/drive/MyDrive/backgrounds_raw'
TEMP_DIR  = '/content/temp_images'
OUT_DRIVE = '/content/drive/MyDrive/backgrounds_triplets'

FRAME_SIZE = 1024
PAD_COLOR  = (24, 24, 24)  # #181818
EXTS       = ('.jpg','.jpeg','.JPG','.JPEG','.webp','.WEBP')

os.makedirs(TEMP_DIR, exist_ok=True)
os.makedirs(OUT_DRIVE, exist_ok=True)

# Clean previous output
for f in os.listdir(OUT_DRIVE):
    os.remove(os.path.join(OUT_DRIVE, f))

print(f"Extracting images from {RAW_DRIVE}...")

# ─────────────────────────────────────────────────────────────────────────────
def is_macos_junk(p: str) -> bool:
    name = os.path.basename(p).lower()
    return (
        '__macosx' in p.lower() or
        name.startswith('._') or
        name == '.ds_store' or
        name.endswith('~')
    )

all_image_paths = []

for zip_name in os.listdir(RAW_DRIVE):
    if not zip_name.lower().endswith('.zip'): continue
    zip_path = os.path.join(RAW_DRIVE, zip_name)
    with zipfile.ZipFile(zip_path, 'r') as z:
        for member in z.namelist():
            if any(member.lower().endswith(e) for e in EXTS) and not is_macos_junk(member):
                z.extract(member, TEMP_DIR)
                all_image_paths.append(os.path.join(TEMP_DIR, member))

print(f"Found {len(all_image_paths)} valid images.")
if len(all_image_paths) < 3:
    raise ValueError("Need at least 3 images!")

# ─────────────────────────────────────────────────────────────────────────────
def add_rounded_corners(img: Image.Image, radius: int) -> Image.Image:
    """Apply rounded corners using gray background."""
    rgba = img.convert('RGBA') if img.mode != 'RGBA' else img
    mask = Image.new('L', rgba.size, 0)
    draw = ImageDraw.Draw(mask)
    draw.rounded_rectangle([(0,0), rgba.size], radius, fill=255)
    result = Image.new('RGBA', rgba.size)
    result.paste(rgba, (0,0))
    result.putalpha(mask)
    bg = Image.new('RGB', result.size, PAD_COLOR)
    bg.paste(result, (0,0), result)
    return bg

# ─────────────────────────────────────────────────────────────────────────────
def center_crop_to_size(img: Image.Image, target_w: int, target_h: int) -> Image.Image:
    """Center-crop image to exactly (target_w, target_h)."""
    w, h = img.size
    if w == target_w and h == target_h:
        return img

    # Scale to cover target
    scale = max(target_w / w, target_h / h)
    new_w = int(w * scale)
    new_h = int(h * scale)
    img_resized = img.resize((new_w, new_h), Image.LANCZOS)

    # Center crop
    left = (new_w - target_w) // 2
    top = (new_h - target_h) // 2
    right = left + target_w
    bottom = top + target_h
    return img_resized.crop((left, top, right, bottom))

# ─────────────────────────────────────────────────────────────────────────────
def create_triplet(img_paths, idx):
    canvas = Image.new('RGB', (FRAME_SIZE, FRAME_SIZE), PAD_COLOR)

    # === EXACT COLUMN DIMENSIONS ===
    col_gap = 20
    total_h_gaps = 2 * col_gap
    col_width = (FRAME_SIZE - 2 * padding_to_edge - total_h_gaps) // 3
    col_height = FRAME_SIZE - 2 * padding_to_top_bottom  # e.g. 1024 - 40 = 984

    x_offsets = [
        padding_to_edge,
        padding_to_edge + col_width + col_gap,
        padding_to_edge + 2 * (col_width + col_gap)
    ]

    for i, path in enumerate(img_paths):
        with Image.open(path) as im:
            img = im.convert('RGB')

        # === CENTER-CROP TO EXACT COLUMN SIZE ===
        img_cropped = center_crop_to_size(img, col_width, col_height)

        # === APPLY ROUNDED CORNERS ===
        img_rounded = add_rounded_corners(img_cropped, corner_radius)

        # === PASTE AT EXACT POSITION (no extra offset) ===
        x = x_offsets[i]
        y = padding_to_top_bottom
        canvas.paste(img_rounded, (x, y))

    return canvas

# ─────────────────────────────────────────────────────────────────────────────
print(f"Generating {output_count} triplet(s)...")
for i in range(output_count):
    selected = random.sample(all_image_paths, 3)
    triplet = create_triplet(selected, i)
    out_path = os.path.join(OUT_DRIVE, f"triplet_{i:03d}.jpg")
    triplet.save(out_path, "JPEG", quality=95)
    print(f"  → {os.path.basename(out_path)}")

# Clean up
shutil.rmtree(TEMP_DIR, ignore_errors=True)

print("\n=== ALL DONE ===")
print(f"Generated {output_count} triplet(s)")
print(f"Column size: {((FRAME_SIZE - 2*padding_to_edge - 40)//3)} × {FRAME_SIZE - 2*padding_to_top_bottom}")
print(f"Horizontal padding: {padding_to_edge}px")
print(f"Vertical padding:   {padding_to_top_bottom}px")
print(f"Column gap:         20px")
print(f"Corner radius:      {corner_radius}px")
print(f"Saved to: {OUT_DRIVE}")

# Show first result
from IPython.display import Image as IPImage, display
display(IPImage(filename=os.path.join(OUT_DRIVE, "triplet_000.jpg")))

Copy the saved filename from above cell ⬆️ and paste in cell below for aesthetic sorting.  

Activate T4 for below cells for faster processing (no data is lost since output is saved to the drive in above cells , and below).

##T4 Stuff

In [ ]:
import os
import zipfile
import shutil
from google.colab import drive

# Mount Google Drive (if not already mounted)
try:
    drive.mount('/content/drive')
except:
    print("Drive already mounted.")

# Define source folder and destination path
source_folder = '/content/manga_on_bg'
destination_zip = '/content/drive/MyDrive/manga_on_bg.zip'

# Create the zip file
print(f"Creating zip file from {source_folder}...")
shutil.make_archive(destination_zip.replace('.zip', ''), 'zip', source_folder)
print(f"Zip file created at {destination_zip}")

In [ ]:
import os
import zipfile
import shutil
from google.colab import drive
from PIL import Image

# Mount Google Drive (if not already mounted)
try:
    drive.mount('/content/drive')
except:
    print("Drive already mounted.")

# Define source folder and destination zip path
source_folder = '/content/drive/MyDrive/backgrounds_cropped3'
destination_zip = '/content/drive/MyDrive/backgrounds_cropped3.zip'

# Ensure the source folder exists
if not os.path.exists(source_folder):
    raise FileNotFoundError(f"Source folder not found: {source_folder}")

# Create the zip file
print(f"Creating zip file from {source_folder}...")

# Get a list of image files in the source folder, sorted by name
image_files = sorted([f for f in os.listdir(source_folder) if f.lower().endswith(('.png', '.jpg', '.jpeg', '.bmp', '.webp'))])

if not image_files:
    print(f"No image files found in {source_folder}. Zip file will not be created.")
else:
    with zipfile.ZipFile(destination_zip, 'w', zipfile.ZIP_DEFLATED) as zipf:
        for i, filename in enumerate(image_files):
            src_path = os.path.join(source_folder, filename)
            # Define the new name inside the zip (1, 2, 3, ...) with original extension
            new_name = f"{i + 1}{os.path.splitext(filename)[1].lower()}"
            try:
                # Use PIL to ensure the image is valid before adding to zip
                with Image.open(src_path) as img:
                    img.verify() # Verify it's an image

                zipf.write(src_path, arcname=new_name)
                # print(f"Added {filename} as {new_name} to zip") # Optional: uncomment for detailed progress
            except Exception as e:
                print(f"Skipping invalid or corrupted image {filename}: {e}")

    print(f"Zip file created at {destination_zip} containing {len(image_files)} images.")

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).
Creating zip file from /content/drive/MyDrive/backgrounds_cropped3...
Zip file created at /content/drive/MyDrive/backgrounds_cropped3.zip containing 325 images.


##Aesthetic sorting using CLIP (T4)

In [ ]:
# --------------------------------------------------------------
# 0. INSTALL & MOUNT
# --------------------------------------------------------------
!pip install -q open_clip_torch torch torchvision pillow tqdm pandas ftfy regex scikit-learn

import zipfile, os, shutil, tempfile, requests, numpy as np
from tqdm import tqdm
import torch, open_clip
from PIL import Image
import glob, pandas as pd
from sklearn.metrics.pairwise import cosine_similarity
from google.colab import drive

drive.mount('/content/drive')

In [ ]:
# --------------------------------------------------------------
# 1. PARAMETERS  (Google-Colab Form UI)
# --------------------------------------------------------------

#@title **Input Settings** { display-mode: "form" }

ZIP_PATH = "/content/drive/MyDrive/manga_on_backgrounds_10852.zip" #@param {type:"string"}
EXTRACT_TO = "/content/dbg_aesthetic_sorted" #@param {type:"string"}
OUT_DIR = "/content/drive/MyDrive/dbg_aesthetic_sorted" #@param {type:"string"}

#@title **Deduplication Settings** { display-mode: "form" }

SIMILARITY_THRESHOLD = 0.9 #@param {type:"slider", min:0.8, max:1.0, step:0.005}
FILESIZE_TOLERANCE    = 0.2 #@param {type:"slider", min:0.0, max:0.4, step:0.01}

#@title **Packing Settings** { display-mode: "form" }

MAX_ZIP_BYTES = 300 #@param {type:"slider", min:50, max:1000, step:50}
MAX_ZIP_BYTES = MAX_ZIP_BYTES * 1024 * 1024   # convert MiB → bytes

# -----------------------------------------------------------------
# (no changes needed below – the rest of the notebook uses these vars)
# -----------------------------------------------------------------
os.makedirs(EXTRACT_TO, exist_ok=True)
os.makedirs(OUT_DIR,    exist_ok=True)

print("Parameters loaded from the form")

In [ ]:
# --------------------------------------------------------------
# 2. EXTRACT ONLY IMAGES (skip if already done)
# --------------------------------------------------------------
if not os.listdir(EXTRACT_TO):
    with zipfile.ZipFile(ZIP_PATH, 'r') as z:
        members = [m for m in z.namelist()
                   if m.lower().split('.')[-1] in {'png','jpg','jpeg','bmp','webp'}]
        for member in tqdm(members, desc='Extracting images'):
            z.extract(member, EXTRACT_TO)
else:
    print("Folder already contains files – skipping extraction.")

In [ ]:
# --------------------------------------------------------------
# 3. LOAD CLIP + AESTHETIC HEAD
# --------------------------------------------------------------
device = "cuda" if torch.cuda.is_available() else "cpu"

clip_model, _, preprocess = open_clip.create_model_and_transforms(
    model_name="ViT-B-32", pretrained="laion400m_e32"
)
clip_model.to(device).eval()

# ---- aesthetic head ------------------------------------------------
AESTHETIC_URL = "https://github.com/LAION-AI/aesthetic-predictor/raw/main/sa_0_4_vit_b_32_linear.pth"
ckpt_path = "/content/laion_aesthetic_vit_b_32.pth"
if not os.path.exists(ckpt_path):
    print("Downloading aesthetic weights …")
    r = requests.get(AESTHETIC_URL); r.raise_for_status()
    open(ckpt_path, 'wb').write(r.content)

aesthetic_head = torch.nn.Linear(512, 1).to(device)
aesthetic_head.load_state_dict(torch.load(ckpt_path, map_location=device))
aesthetic_head.eval()
print("CLIP + aesthetic head ready")

In [ ]:
# --------------------------------------------------------------
# 4. SCORE ALL IMAGES
# --------------------------------------------------------------
image_paths = glob.glob(f"{EXTRACT_TO}/**/*.*", recursive=True)
image_paths = [p for p in image_paths
               if p.lower().split('.')[-1] in {'png','jpg','jpeg','bmp','webp'}]

results = []
with torch.no_grad():
    for p in tqdm(image_paths, desc="Scoring"):
        try:
            img = Image.open(p).convert("RGB")
            x   = preprocess(img).unsqueeze(0).to(device)
            emb = clip_model.encode_image(x)               # (1,512)

            logit = aesthetic_head(emb)
            score = torch.sigmoid(logit).item() * 10.0     # 0-10 scale

            results.append({'path': p, 'score': score})
        except Exception as e:
            print(f"Skip {p}: {e}")

df = pd.DataFrame(results)
df = df.sort_values('score', ascending=False).reset_index(drop=True)
print(f"Scored {len(df)} images | best {df['score'].iloc[0]:.2f} | worst {df['score'].iloc[-1]:.2f}")

In [ ]:
# --------------------------------------------------------------
# 5. DEDUPLICATION (file-size + CLIP similarity)
# --------------------------------------------------------------
@torch.no_grad()
def get_clip_embedding(p):
    try:
        img = Image.open(p).convert("RGB")
        x   = preprocess(img).unsqueeze(0).to(device)
        emb = clip_model.encode_image(x)
        emb = emb / emb.norm(dim=-1, keepdim=True)
        return emb.cpu().numpy().flatten()
    except Exception:
        return None

# ---- group by approximate size ------------------------------------
size_groups = {}
for p in df['path']:
    sz = os.path.getsize(p)
    key = round(sz * (1 / (1 + FILESIZE_TOLERANCE)))
    size_groups.setdefault(key, []).append(p)

kept_paths = []
for key, group in tqdm(size_groups.items(), desc="Deduplicate groups"):
    if len(group) == 1:
        kept_paths.append(group[0])
        continue

    # compute embeddings only for this small group
    embeddings = []
    valid_paths = []
    for p in group:
        emb = get_clip_embedding(p)
        if emb is not None:
            embeddings.append(emb)
            valid_paths.append(p)

    if len(embeddings) <= 1:
        kept_paths.extend(valid_paths)
        continue

    embeddings = np.stack(embeddings)
    sim = cosine_similarity(embeddings)

    keep = [True] * len(valid_paths)
    for i in range(len(valid_paths)):
        if not keep[i]: continue
        for j in range(i+1, len(valid_paths)):
            if sim[i, j] >= SIMILARITY_THRESHOLD:
                keep[j] = False

    for idx, k in enumerate(keep):
        if k:
            kept_paths.append(valid_paths[idx])

# ---- filter original dataframe ------------------------------------
df_clean = df[df['path'].isin(kept_paths)].copy()
df_clean = df_clean.sort_values('score', ascending=False).reset_index(drop=True)
print(f"After deduplication: {len(df_clean)} images (removed {len(df)-len(df_clean)} duplicates)")

Deduplicate groups: 100%|██████████| 234/234 [00:00<00:00, 1106501.84it/s]

After deduplication: 234 images (removed 0 duplicates)


In [ ]:
# --------------------------------------------------------------
# 6. PACK CLEANED IMAGES INTO ≤300 MiB ZIPs
# --------------------------------------------------------------
temp_dir = '/content/zip_temp'
os.makedirs(temp_dir, exist_ok=True)

current_files = []      # (temp_path, arcname)
current_size  = 0
zip_idx       = 1

def finish_zip():
    global zip_idx, current_size, current_files
    if not current_files: return
    zip_path = f"{OUT_DIR}/mia_panels_part_{zip_idx:03d}.zip"
    with zipfile.ZipFile(zip_path, 'w', zipfile.ZIP_DEFLATED) as z:
        for src, arc in current_files:
            z.write(src, arc)
    mb = os.path.getsize(zip_path) / 1e6
    print(f"Saved {zip_path}  ({len(current_files)} files, {mb:.1f} MB)")
    for src, _ in current_files:
        os.remove(src)
    current_files = []
    current_size = 0
    zip_idx += 1

for idx, row in enumerate(tqdm(df_clean.itertuples(), total=len(df_clean), desc="Packing")):
    src  = row.path
    rank = idx + 1
    ext  = os.path.splitext(src)[1].lower()
    tmp  = f"{temp_dir}/{rank}{ext}"
    shutil.copyfile(src, tmp)

    fsize = os.path.getsize(tmp)
    if current_size + fsize > MAX_ZIP_BYTES and current_files:
        finish_zip()

    current_files.append((tmp, f"{rank}{ext}"))
    current_size += fsize

finish_zip()
shutil.rmtree(temp_dir, ignore_errors=True)

# --------------------------------------------------------------
# 7. SAVE SCORE CSV (only the kept images)
# --------------------------------------------------------------
df_clean.to_csv(f"{OUT_DIR}/aesthetic_scores_clean.csv", index=False)
print("\nAll done! Cleaned ZIPs + CSV are in:", OUT_DIR)

Packing: 100%|██████████| 234/234 [00:00<00:00, 843.77it/s] 


Saved /content/drive/MyDrive/dbg_aesthetic_sorted/mia_panels_part_001.zip  (234 files, 226.5 MB)

All done! Cleaned ZIPs + CSV are in: /content/drive/MyDrive/dbg_aesthetic_sorted


##Sort images into folders using CLIP image feature extraction (T4)

In [ ]:
#@markdown Unzip training data from drive to /content/ (if required)
path = '/content/drive/MyDrive/training_data_66708.zip' #@param {type:'string'}

%cd /content/
!unzip  {path}

In [ ]:
!pip install ftfy regex tqdm
!pip install git+https://github.com/openai/CLIP.git
!pip install scikit-learn matplotlib pillow umap-learn  # UMAP is optional for 2D visualization

Load Images and Extract CLIP Embeddings

Upload your images the normal way ( `/content/`) prior to running this cell.

This code loads all images (supports JPG, PNG, etc.), preprocesses them, and extracts 512-dimensional embeddings using the ViT-B/32 CLIP model.

In [ ]:
!pip install open_clip_torch

import os
import numpy as np
import torch
import open_clip
from PIL import Image

# Configuration
image_dir = '/content/'  #@param {type:'string'}
device = "cuda" if torch.cuda.is_available() else "cpu"
model_name = "ViT-B-32"  # Available per error message
pretrained = "laion400m_e32"  # Robust pretrained weights

# Load OpenCLIP model
model, _, preprocess = open_clip.create_model_and_transforms(model_name, pretrained=pretrained)
model.to(device)
model.eval()

# Load images and extract embeddings
embeddings = []
image_paths = []
image_names = []

# Recursively find images in subdirectories, excluding /content/drive/
for root, _, files in os.walk(image_dir):
    if '/drive/' in root:  # Explicitly skip any directory containing '/drive/'
        continue
    for filename in files:
        if filename.lower().endswith(('.png', '.jpg', '.jpeg', '.gif', '.bmp')):
            img_path = os.path.join(root, filename)
            try:
                image = preprocess(Image.open(img_path)).unsqueeze(0).to(device)
                with torch.no_grad():
                    embedding = model.encode_image(image)
                embeddings.append(embedding.cpu().numpy().flatten())
                image_paths.append(img_path)
                image_names.append(filename)
                #print(f"Processed: {filename}")
            except Exception as e:
                print(f"Error processing {filename}: {e}")

embeddings = np.array(embeddings)
print(f"Extracted embeddings for {len(embeddings)} images. Shape: {embeddings.shape}")

Perform Clustering
We'll use K-Means clustering on the embeddings. You can choose the number of clusters (`n_clusters`) based on your dataset size (e.g., try 5-10). We'll also compute the silhouette score to evaluate cluster quality (higher is better).

For visualization, we'll optionally reduce dimensions to 2D using UMAP.

In [ ]:
from umap import UMAP  # For 2D projection (optional)
import os
import numpy as np
import torch
import clip
from PIL import Image
import matplotlib.pyplot as plt
from sklearn.cluster import KMeans
from sklearn.metrics import silhouette_score
import warnings
warnings.filterwarnings('ignore')
#@markdown Choose number of clusters (experiment with this)
n_clusters = 100  # @param {type:'slider' , min:1 , max:200, step:1}

# Perform K-Means clustering
kmeans = KMeans(n_clusters=n_clusters, random_state=42, n_init=10)
cluster_labels = kmeans.fit_predict(embeddings)

# Evaluate clustering quality
sil_score = silhouette_score(embeddings, cluster_labels)
print(f"Silhouette Score: {sil_score:.3f} (closer to 1 is better)")

# Optional: 2D visualization with UMAP
reducer = UMAP(random_state=42, n_components=2)
embed_2d = reducer.fit_transform(embeddings)

plt.figure(figsize=(10, 8))
scatter = plt.scatter(embed_2d[:, 0], embed_2d[:, 1], c=cluster_labels, cmap='tab10', s=50)
plt.colorbar(scatter)
plt.title(f'2D UMAP Projection of CLIP Embeddings (K={n_clusters} Clusters)')
plt.xlabel('UMAP 1')
plt.ylabel('UMAP 2')
plt.show()

In [ ]:
import shutil
import os
from PIL import Image

# Create output directories
output_dir = '/content/clusters'  # Output base directory
os.makedirs(output_dir, exist_ok=True)

move_files = False  # Set to True to move files, False to copy

# Create directories for each cluster
for i in range(n_clusters):
    cluster_dir = os.path.join(output_dir, f'cluster_{i}')
    os.makedirs(cluster_dir, exist_ok=True)

# Form inputs using Colab's # @param
output_format = "JPEG"  # @param ["JPEG", "PNG", "WEBP"]
quality = 100  # @param {type:"slider", min:0, max:100, step:1}

# Function to convert and save images
for idx, label in enumerate(cluster_labels):
    src_path = image_paths[idx]  # Use full path
    # Create destination filename with selected extension
    dst_filename = os.path.splitext(image_names[idx])[0] + f'.{output_format.lower()}'
    dst_path = os.path.join(output_dir, f'cluster_{label}', dst_filename)

    try:
        # Open and convert image
        with Image.open(src_path).convert('RGB') as img:
            if output_format == 'JPEG':
                img.save(dst_path, 'JPEG', quality=quality, optimize=True)
            elif output_format == 'PNG':
                # PNG compression: 0 (max compression) to 9 (no compression)
                # Map quality 0-100 to PNG compression 9-0
                png_compression = int(9 - (quality / 100 * 9))
                img.save(dst_path, 'PNG', compress_level=png_compression)
            elif output_format == 'WEBP':
                img.save(dst_path, 'WEBP', quality=quality)

            if move_files:
                os.remove(src_path)  # Delete original if moving
            print(f"Assigned {image_names[idx]} as {dst_filename} to cluster_{label}")
    except Exception as e:
        print(f"Error converting {image_names[idx]} to {output_format}: {e}")

print(f"Images sorted into {n_clusters} clusters in '{output_dir}' as .{output_format.lower()}")

In [ ]:
from PIL import Image
import matplotlib.pyplot as plt
import os

def display_cluster_samples(cluster_dir, n_samples=3):
    # Check if cluster directory exists
    if not os.path.exists(cluster_dir):
        print(f"Cluster directory {cluster_dir} does not exist")
        return

    # Updated to include .jpg, .png, and .webp files
    images = [f for f in os.listdir(cluster_dir) if f.lower().endswith(('.jpg', '.jpeg', '.png', '.webp'))][:n_samples]
    if not images:
        print(f"No images in {cluster_dir}")
        return

    fig, axs = plt.subplots(1, len(images), figsize=(5 * len(images), 5))
    if len(images) == 1:
        axs = [axs]
    for j, img_file in enumerate(images):
        img_path = os.path.join(cluster_dir, img_file)
        try:
            img = Image.open(img_path).convert('RGB')  # Ensure RGB for display
            axs[j].imshow(img)
            axs[j].set_title(img_file)
            axs[j].axis('off')
        except Exception as e:
            print(f"Error displaying {img_file}: {e}")
    plt.show()

# Create output directories
output_dir = '/content/clusters'  # Output base directory

# Check if output directory exists
if not os.path.exists(output_dir):
    print(f"Output directory {output_dir} does not exist")
else:
    # Display samples from each cluster
    for i in range(n_clusters):  # Ensure n_clusters is defined
        cluster_dir = os.path.join(output_dir, f'cluster_{i}')
        print(f"\nSamples from Cluster {i}:")
        display_cluster_samples(cluster_dir)

In [ ]:
import shutil
%cd /content/
#@markdown Remove cluster_N.  You can set multiple indices at once 1,4,5,9,...
nums ='1,5,9,12,16,18,20,22,31,33,34,36,37,38,53,58,60,62,66,71,74,79,85,87,88,92,93,95,98'#@param {type:'string'}

for num in nums.split(','):
  if num.strip() == '': continue
  shutil.rmtree(f'/content/clusters/cluster_{num.strip()}')

/content


Sort Images into Clusters
This creates subdirectories for each cluster and moves/copies the images there. Set `move_files=True` to move (or False to copy).

Visualize Sample Images per Cluster
Display a few sample images from each cluster to inspect the results.

In [ ]:
#@markdown Upload to Google Drive as .zip folder (Be mindful of Google Drive Terms of Service)
drive_folder_name = 'my_clusters' # @param {type:'string'}

%cd /content/
!zip -r /content/drive/MyDrive/{drive_folder_name}.zip {output_dir}

